In [5]:
import validation_library as veri   
import os  
import importlib

results_csv = 'reports/aggregated/validation_results_DeepSeek.csv'
results_json = "reports/aggregated/DeepSeek/contracts_PVP.json"
fixed_results_csv = 'reports/aggregated/validation_results_DeepSeek_fixed.csv'

patches_dir = 'reports/aggregated/DeepSeek/patches_DeepSeek/'

In [6]:

os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"

importlib.reload(veri)

counter_greater_than_200 = 0

contract_lines_4X = []

contracts_4X = veri.get_files("smartbugs-curated/0.4.x/contracts/dataset")

for contract_path, contract_name in contracts_4X:
    contract, line = veri.find_occurrences(contract_path, "// <yes> <report>")
    if contract.count('\n') > 200:
        counter_greater_than_200 += 1 
    else:
        clean_contract = veri.replace_lines_with_string(contract, line, '')
        contract_lines_4X.append((contract_name, clean_contract, line))

veri.print_json_report("reports/aggregated/contract_no_comment.json", contract_lines_4X)
veri.print_txt_report("reports/aggregated/contract_no_comment.txt", contract_lines_4X)


In [7]:


importlib.reload(veri)
contracts_with_results = veri.read_json_report(results_json)
 
contract_lines = veri.read_json_report("reports/aggregated/contract_no_comment.json") 


In [8]:
from tqdm import tqdm

importlib.reload(veri)
headers = [
    'Solidity_file_name',
    'vulnerability_type',
    'vulnerable_line_number',
    'vulnerability_function_entry_line',
    'vulnerability_function_end_line',
    'VL',
    'pre_post',
    'pre',
    'post',
    'pre_VL_post',
    'pre_VL',
    'VL_post'
]

veri.create_csv_if_not_exists(results_csv, headers)

def evaluate_contracts(contract_lines, patch, contract_file=None):
    contract_name = contract_lines[0]
    CONTRACTS_ROOT = "smartbugs-curated/0.4.x/contracts/dataset"
    TESTS_ROOT = "smartbugs-curated/0.4.x/test"
    if contract_file is None:
        contract_file = veri.find_contract_path(CONTRACTS_ROOT, contract_name)
    print(f'contract_file is: {contract_file}')
    test_file = veri.find_contract_path(TESTS_ROOT, contract_name.replace(".sol", "_test.js"))
    print(f'test_file is: {test_file}')
    # ... rest of code ...

# Ensure contract_file is always the resolved path, and never call find_contract_path on it again.
# Add progress bar for contracts
for contract in tqdm(contract_lines, desc="Processing contracts"): 
        contract_name = contract[0]
        contract_code = contract[1]
        lines = contract[2]

        # Always use basename for search, and only call find_contract_path once per contract.
        contract_file = veri.find_contract_path("smartbugs-curated", os.path.basename(contract_name))
        import re
        # Add progress bar for patches per contract
        for contract_patch_VL in tqdm(contracts_with_results[contract[0]], desc=f"Patches for {contract_name}", leave=False): 
                contract_patch = contract_patch_VL[0]
                VL_line, VL_require = contract_patch_VL[1]["VL"]
                if 'require(require(' in VL_require:
                      print(f'VL_require is: \n{VL_require}\n')
                      #VL_require = VL_require.replace('require(require(', 'require(').replace('););', ');')
                      
                      VL_require = re.sub(r'(require\()+', 'require(', VL_require)
                      VL_require = re.sub(r'(\);)+', ');', VL_require)
                pre_line, pre_require = contract_patch_VL[1]["pre"]
                if 'require(require(' in pre_require:
                      print(f'pre_require is: \n{pre_require}\n')
                      #pre_require = pre_require.replace('require(require(', 'require(').replace('););', ');')
                      pre_require = re.sub(r'(require\()+', 'require(', pre_require)
                      pre_require = re.sub(r'(\);)+', ');', pre_require)
                post_line, post_require = contract_patch_VL[1]["post"]
                if 'require(require(' in post_require:
                      print(f'post require is: \n{post_require}\n')
                      #post_require = post_require.replace('require(require(', 'require(').replace('););', ');')
                      post_require = re.sub(r'(require\()+', 'require(', post_require)
                      post_require = re.sub(r'(\);)+', ');', post_require)

                contract_patch = veri.replace_lines_with_string(contract_patch, [VL_line], VL_require)
                patch_VL = (contract_patch, VL_line, VL_require)
                # VL
                print(f'>>>>>>>>>>>>>>>>> <<<<<<<<<<<<< patch_vl is: {patch_VL}')
                no_test, result_VL = veri.evaluate_contracts(contract, patch_VL, contract_file=contract_file)
                if no_test:
                        break

                # Pre
                contract_patch_pre = veri.insert_empty_line(contract_code, pre_line)
                contract_patch_pre = veri.replace_lines_with_string(contract_patch_pre, [pre_line], pre_require)
                patch_pre = (contract_patch_pre, pre_line, pre_require)
                no_test, result_pre = veri.evaluate_contracts(contract, patch_pre, contract_file=contract_file)

                # Post
                contract_patch_post = veri.insert_empty_line(contract_code, post_line)
                contract_patch_post = veri.replace_lines_with_string(contract_patch_post, [post_line], post_require)
                patch_post = (contract_patch_post, post_line, post_require)
                no_test, result_post = veri.evaluate_contracts(contract, patch_post, contract_file=contract_file)

                # Pre + Post
                contract_patch_pre_post = veri.insert_empty_line(contract_code, post_line)
                contract_patch_pre_post = veri.replace_lines_with_string(contract_patch_pre_post, [post_line], post_require)
                contract_patch_pre_post = veri.insert_empty_line(contract_patch_pre_post, pre_line)
                contract_patch_pre_post = veri.replace_lines_with_string(contract_patch_pre_post, [pre_line], pre_require)

                patch_lines = f"{pre_line},{post_line}"
                PP_require = f"{pre_require},{post_require}"
                patch_pre_post = (contract_patch_pre_post, patch_lines, PP_require)
                no_test, result_pre_post = veri.evaluate_contracts(contract, patch_pre_post, contract_file=contract_file)

                # Pre + VL + Post (PVP)
                contract_patch_PVP = veri.insert_empty_line(contract_patch, post_line)
                contract_patch_PVP = veri.replace_lines_with_string(contract_patch_PVP, [post_line], post_require)
                contract_patch_PVP = veri.insert_empty_line(contract_patch_PVP, pre_line)
                contract_patch_PVP = veri.replace_lines_with_string(contract_patch_PVP, [pre_line], pre_require)

                patch_lines = f"{pre_line},{VL_line},{post_line}"
                PVP_require = f"{pre_require},{VL_require},{post_require}"
                patch_PVP = (contract_patch_PVP, patch_lines, PVP_require)
                no_test, result_PVP = veri.evaluate_contracts(contract, patch_PVP, contract_file=contract_file)

                # Pre + VL (PV)
                contract_patch_PV = veri.insert_empty_line(contract_patch, pre_line)
                contract_patch_PV = veri.replace_lines_with_string(contract_patch_PV, [pre_line], pre_require)

                patch_lines = f"{pre_line},{VL_line}"
                PV_require = f"{pre_require},{VL_require}"
                patch_PV = (contract_patch_PV, patch_lines, PV_require)
                no_test, result_PV = veri.evaluate_contracts(contract, patch_PV, contract_file=contract_file)

                # VL + Post (VP)
                contract_patch_VP = veri.insert_empty_line(contract_patch, post_line)
                contract_patch_VP = veri.replace_lines_with_string(contract_patch_VP, [post_line], post_require)

                patch_lines = f"{VL_line},{post_line}"
                VP_require = f"{VL_require},{post_require}"
                patch_VP = (contract_patch_VP, patch_lines, VP_require)
                no_test, result_VP = veri.evaluate_contracts(contract, patch_VP, contract_file=contract_file)

                type_V = veri.get_directory_name(contract_name,"sb-heists/smartbugs-curated")

                row = {
                        'Solidity_file_name': contract_name,
                        'vulnerability_type': type_V,
                        'vulnerable_line_number': VL_line,
                        'vulnerability_function_entry_line': pre_line - 1,
                        'vulnerability_function_end_line': post_line,
                        'VL': result_VL,
                        'pre_post': result_pre_post,
                        'pre': result_pre,
                        'post': result_post,
                        'pre_VL_post': result_PVP,
                        'pre_VL': result_PV,
                        'VL_post': result_VP
                }

                veri.append_row(results_csv, headers, row)

                strategy_patch_map = {
                        'VL': contract_patch, 
                        'pre': contract_patch_pre,
                        'post': contract_patch_post,
                        'pre_post': contract_patch_pre_post,
                        'pre_VL_post': contract_patch_PVP,
                        'pre_VL': contract_patch_PV,
                        'VL_post': contract_patch_VP
                }

                veri.save_patches_by_strategy(
                        output_dir=patches_dir,
                        contract_name=contract_name,
                        strategy_patch_map=strategy_patch_map
                )

CSV file 'reports/aggregated/validation_results_DeepSeek.csv' created successfully in Excel-friendly format.


Processing contracts:   0%|          | 0/131 [00:00<?, ?it/s]

VL_require is: 
require(require(msg.value >= 1 ether););

pre_require is: 
require(require(msg.value >= 1 ether););

post require is: 
require(require(msg.value >= 1 ether););

>>>>>>>>>>>>>>>>> <<<<<<<<<<<<< patch_vl is: ('/*\n * @source: https://github.com/SmartContractSecurity/SWC-registry/blob/master/test_cases/weak_randomness/random_number_generator.sol\n * @author: -\n * @vulnerable_at_lines: 12,18,20,22\n */\n\npragma solidity ^0.4.25;\n\n// Based on TheRun contract deployed at 0xcac337492149bDB66b088bf5914beDfBf78cCC18.\ncontract RandomNumberGenerator {\nrequire(msg.value >= 1 ether);\n  uint256 private salt =  block.timestamp;\n\n  function random(uint max) view private returns (uint256 result) {\n    // Get the best seed for randomness\n    uint256 x = salt * 100 / max;\n\n    uint256 y = salt * block.number / (salt % 5);\n\n    uint256 seed = block.number / 3 + (salt % 300) + y;\n\n    uint256 h = uint256(blockhash(seed));\n    // Random number between 1 and max\n    return 

Patches for lottery.sol:   0%|          | 0/2 [00:00<?, ?it/s]

VL_require is: 
require(require(msg.value == 500 finney););

pre_require is: 
require(require(msg.value == 500 finney););

post require is: 
require(require(msg.value == 500 finney););

>>>>>>>>>>>>>>>>> <<<<<<<<<<<<< patch_vl is: ("/*\n * @article: https://blog.positive.com/predicting-random-numbers-in-ethereum-smart-contracts-e5358c6b8620\n * @source: https://etherscan.io/address/0x80ddae5251047d6ceb29765f38fed1c0013004b7#code\n * @vulnerable_at_lines: 38,42\n * @author: -\n */\n\n //added pragma version\n  pragma solidity ^0.4.0;\n  \n contract Lottery {\n     event GetBet(uint betAmount, uint blockNumber, bool won);\n\n     struct Bet {\n         uint betAmount;\n         uint blockNumber;\n         bool won;\n     }\n\n     address private organizer;\n     Bet[] private bets;\n\n     // Create a new lottery with numOfBets supported bets.\n     function Lottery() {\n         organizer = msg.sender;\n     }\n\n     // Fallback function returns ether\n     function() {\n         thro

...

VL_require is: 
require(require(msg.sender.call.value(msg.value)()););

pre_require is: 
require(require(msg.value >= 0.5 ether););

post require is: 
require(require(msg.sender.call.value(msg.value)()););

>>>>>>>>>>>>>>>>> <<<<<<<<<<<<< patch_vl is: ('/*\n * @source: http://blockchain.unica.it/projects/ethereum-survey/attacks.html#governmental\n * @author: -\n * @vulnerable_at_lines: 27\n */\n\n//added pragma version\npragma solidity ^0.4.0;\n\ncontract Governmental {\n  address public owner;\n  address public lastInvestor;\n  uint public jackpot = 1 ether;\n  uint public lastInvestmentTimestamp;\n  uint public ONE_MINUTE = 1 minutes;\n\n  function Governmental() {\n    owner = msg.sender;\n    if (msg.value<1 ether) throw;\n  }\n\n  function invest() {\n    if (msg.value<jackpot/2) throw;\n    lastInvestor = msg.sender;\n    jackpot += msg.value/2;\nrequire(msg.sender.call.value(msg.value)());\n    lastInvestmentTimestamp = block.timestamp;\n  }\n\n  function resetInvestment() {\n  

Patches for timed_crowdsale.sol:   0%|          | 0/1 [00:00<?, ?it/s]

VL_require is: 
require(require(now >= 1546300800););

pre_require is: 
require(require(now >= 1546300800););

post require is: 
require(require(now >= 1546300800););

>>>>>>>>>>>>>>>>> <<<<<<<<<<<<< patch_vl is: ('/*\n * @source: https://github.com/SmartContractSecurity/SWC-registry/blob/master/test_cases/timestamp_dependence/timed_crowdsale.sol\n * @author: -\n * @vulnerable_at_lines: 13\n */\n\npragma solidity ^0.4.25;\n\ncontract TimedCrowdsale {\n  // Sale should finish exactly at January 1, 2019\n  function isSaleFinished() view public returns (bool) {\nrequire(now >= 1546300800);\n    return block.timestamp >= 1546300800;\n  }\n}', 12, 'require(now >= 1546300800);')
contract_file is: contracts/dataset/time_manipulation/timed_crowdsale.sol
test_file is: test/time_manipulation/timed_crowdsale_test.js

=== Evaluating patches for contract: timed_crowdsale.sol ===
evaluation_results/timed_crowdsale.sol_patch_line_12.sol
------->. subprocess result: Base directory: ../smartbugs-curate

Processing contracts: 100%|██████████| 131/131 [57:05<00:00, 26.15s/it]96s/it]

------->. subprocess result: Base directory: ../smartbugs-curated/0.4.x
Executing command:  npx hardhat compile
Now using node v22.19.0 (npm v10.9.3)
Hardhat only supports ESM projects.

Please make sure you have `"type": "module"` in your package.json.

You can set it automatically by running:

npm pkg set type="module"



Running tests for contract: contracts/dataset/time_manipulation/timed_crowdsale.sol with patch: /Users/mojtabaeshghie/projects/FLAMES/raw-validation-results/sb-heists/evaluation_results/timed_crowdsale.sol_patch_line_12,14.sol
Executing command:  npx hardhat compile
Now using node v22.19.0 (npm v10.9.3)
Hardhat only supports ESM projects.

Please make sure you have `"type": "module"` in your package.json.

You can set it automatically by running:

npm pkg set type="module"



Executing command:  npx hardhat test test/time_manipulation/timed_crowdsale_test.js
Now using node v22.19.0 (npm v10.9.3)
Hardhat only supports ESM projects.

Please make sure you have `"type":

***Remove junk results with require(false) or \n***

In [ ]:

importlib.reload(veri)

df = veri.produce_dataframe_from_csv(results_csv)
contracts_with_results = veri.read_json_report(results_json)

for index, row in df.iterrows():
    solidity_file = row['Solidity_file_name']
    
    for contracts in contracts_with_results.get(solidity_file, []):
        VL_line, VL_require = contracts[1]["VL"]
        pre_line, pre_require = contracts[1]["pre"]
        post_line, post_require = contracts[1]["post"]
        '''print(VL_line, row['vulnerable_line_number'])
        print(pre_line, row['vulnerability_function_entry_line'])
        print(post_line, row['vulnerability_function_end_line'])'''

        if (
            VL_line == row['vulnerable_line_number'] and
            pre_line == row['vulnerability_function_entry_line'] + 1 and
            post_line == row['vulnerability_function_end_line']
        ):
            
            if "require(false);" in VL_require or "\n" in VL_require:
                df.loc[index, 'VL'] = str(row['VL']).replace('True', 'False')
                df.loc[index, 'pre_VL_post'] = str(row['pre_VL_post']).replace('True', 'False')
                df.loc[index, 'pre_VL'] = str(row['pre_VL']).replace('True', 'False')
                df.loc[index, 'VL_post'] = str(row['VL_post']).replace('True', 'False')

            if "require(false);" in pre_require or "\n" in pre_require:
                df.loc[index, 'pre'] = str(row['pre']).replace('True', 'False')
                df.loc[index, 'pre_VL_post'] = str(row['pre_VL_post']).replace('True', 'False')
                df.loc[index, 'pre_VL'] = str(row['pre_VL']).replace('True', 'False')
                df.loc[index, 'pre_post'] = str(row['pre_post']).replace('True', 'False')

            if "require(false);" in post_require or "\n" in post_require:
                df.loc[index, 'post'] = str(row['post']).replace('True', 'False')
                df.loc[index, 'pre_VL_post'] = str(row['pre_VL_post']).replace('True', 'False')
                df.loc[index, 'VL_post'] = str(row['VL_post']).replace('True', 'False')
                df.loc[index, 'pre_post'] = str(row['pre_post']).replace('True', 'False')

df.to_csv(fixed_results_csv, index=False, sep=';')
  
        